# Deep Q-Learning 

For this assignment we will implement the Deep Q-Learning algorithm with Experience Replay as described in breakthrough paper __"Playing Atari with Deep Reinforcement Learning"__. We will train an agent to play the famous game of __Breakout__.

In [1]:
import sys
import gym
import torch
import pylab
import random
import numpy as np
import time
from collections import deque
from datetime import datetime
from copy import deepcopy
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
from torch.autograd import Variable
from utils import *
from agent import *
from model import *
from config import *
from env import GameEnv
%matplotlib inline
%load_ext autoreload
%autoreload 2

## Understanding the environment

In the following cell, we initialise our game of __Breakout__ and you can see how the environment looks like. For further documentation of the of the environment refer to https://gym.openai.com/envs. 

In [2]:
envs = []
for i in range(num_envs):
    envs.append(GameEnv('SpaceInvadersDeterministic-v4'))
#env.render()

/usr/local/lib/python3.5/dist-packages/skimage/transform/_warps.py:110: UserWarning: Anti-aliasing will be enabled by default in skimage 0.15 to avoid aliasing artifacts when down-sampling images.
  warn("Anti-aliasing will be enabled by default in skimage 0.15 to "


In [3]:
number_lives = envs[0].life
state_size = envs[0].observation_space.shape
action_size = envs[0].action_space.n
rewards, episodes = [], []

## Creating a DQN Agent

Here we create a DQN Agent. This agent is defined in the __agent.py__. The corresponding neural network is defined in the __model.py__. 

__Evaluation Reward__ : The average reward received in the past 100 episodes/games.

__Frame__ : Number of frames processed in total.

__Memory Size__ : The current size of the replay memory.

In [ ]:
agent = Agent(action_size)
evaluation_reward = deque(maxlen=evaluation_reward_length)
frame = 0
memory_size = 0


### Main Training Loop

In [ ]:
vis_env_idx = 0
vis_env = envs[vis_env_idx]
e = 0
frame = 0
while (e < EPISODES):
    step = 0
    assert(num_envs * env_mem_size == train_frame)
    frame_next_vals = []
    for i in range(num_envs):
        env = envs[i]
        #history = env.history
        #life = env.life
        #state, reward, done, info = [env.state, env.reward, env.done, env.info]
        for j in range(env_mem_size):
            step += 1
            frame += 1
            
            curr_state = env.history[3,:,:]
            action, value = agent.get_action(np.float32(env.history[:4,:,:]) / 255.)
            
            next_state, env.reward, env.done, env.info = env.step(action)
            
            if (i == vis_env_idx):
                vis_env._env.render()
            
            frame_next_state = get_frame(next_state)
            env.history[4,:,:] = frame_next_state
            terminal_state = check_live(env.life, env.info['ale.lives'])
            
            env.life = env.info['ale.lives']
            r = env.reward
            
            agent.memory.push(i, deepcopy(curr_state), action, r, terminal_state, value, 0, 0)
            if (j == env_mem_size-1):
                _, frame_next_val = agent.get_action(np.float32(env.history[1:,:,:]) / 255.)
                frame_next_vals.append(frame_next_val)
            env.score += r
            env.history[:4, :, :] = env.history[1:,:,:]
            
            if (env.done):
                if (e % 50 == 0):
                    print('now time : ', datetime.now())
                    rewards.append(np.mean(evaluation_reward))
                    episodes.append(e)
                    pylab.plot(episodes, rewards, 'b')
                    pylab.savefig("./save_graph/spaceinvaders_ppo.png")
                    torch.save(agent.policy_net, "./save_model/spaceinvaders_ppo")
                e += 1
                print("episode:", e, "  score:", env.score,  " epsilon:", agent.epsilon, "   steps:", step,
                  " evaluation reward:", np.mean(evaluation_reward))
                env.done = False
                evaluation_reward.append(env.score)
                env.score = 0
                env.history = np.zeros([5,84,84], dtype=np.uint8)
                env.state = env.reset()
                env.life = number_lives
                get_init_state(env.history, env.state)
                
                
                
    agent.train_policy_net(frame, frame_next_vals)
    agent.update_target_net()

'''
for e in range(EPISODES):
    done = False
    score = 0

    history = np.zeros([5, 84, 84], dtype=np.uint8)
    step = 0
    d = False
    state = env.reset()
    life = number_lives

    get_init_state(history, state)

    while not done:
        step += 1
        frame += 1
        if render_breakout:
            env.render()

        # Select and perform an action
        curr_state = history[3,:,:]
        action, value = agent.get_action(np.float32(history[:4, :, :]) / 255.)

        
        next_state, reward, done, info = env.step(action)

        frame_next_state = get_frame(next_state)
        history[4, :, :] = frame_next_state
        terminal_state = check_live(life, info['ale.lives'])

        life = info['ale.lives']
        #r = np.clip(reward, -1, 1)
        r = reward
        """
        if terminal_state:
            r -= 20
        """
        # Store the transition in memory 
        
        agent.memory.push(deepcopy(curr_state), action, r, terminal_state, value, 0, 0)
        # Start training after random sample generation
        if(frame % train_frame == 0):
            _, frame_next_val = agent.get_action(np.float32(history[1:, :, :]) / 255.)
            agent.train_policy_net(frame, frame_next_val)
            # Update the target network
            agent.update_target_net()
        score += r
        history[:4, :, :] = history[1:, :, :]

        if frame % 50000 == 0:
            print('now time : ', datetime.now())
            rewards.append(np.mean(evaluation_reward))
            episodes.append(e)
            pylab.plot(episodes, rewards, 'b')
            pylab.savefig("./save_graph/spaceinvaders_ppo.png")
            torch.save(agent.policy_net, "./save_model/spaceinvaders_ppo")

        if done:
            evaluation_reward.append(score)
            # every episode, plot the play time
            print("episode:", e, "  score:", score, "  memory length:",
                  len(agent.memory), "  epsilon:", agent.epsilon, "   steps:", step,
                  "    evaluation reward:", np.mean(evaluation_reward))

            # if the mean of scores of last 10 episode is bigger than 400
            # stop training
            if np.mean(evaluation_reward) > 700 and len(evaluation_reward) > 40:
                torch.save(agent.policy_net, "./save_model/spaceinvaders_ppo")
                sys.exit()
'''

/home/sigai/Documents/Projects/Object-Recognition/assignment5_materials/Assignment5_PPO/Assignment5/model.py:45: UserWarning: Implicit dimension choice for softmax has been deprecated. Change the call to include dim=X as an argument.
  probs = F.softmax(x[:,:self.action_size] - torch.max(x[:,:self.action_size],1)[0].unsqueeze(1))
/usr/local/lib/python3.5/dist-packages/skimage/transform/_warps.py:110: UserWarning: Anti-aliasing will be enabled by default in skimage 0.15 to avoid aliasing artifacts when down-sampling images.
  warn("Anti-aliasing will be enabled by default in skimage 0.15 to "


Training network. lr: 0.000250. clip: 0.100000


/home/sigai/Documents/Projects/Object-Recognition/assignment5_materials/Assignment5_PPO/Assignment5/agent.py:254: UserWarning: invalid index of a 0-dim tensor. This will be an error in PyTorch 0.5. Use tensor.item() to convert a 0-dim tensor to a Python number
  pol_loss += pol_avg.detach().cpu()[0]
/home/sigai/Documents/Projects/Object-Recognition/assignment5_materials/Assignment5_PPO/Assignment5/agent.py:255: UserWarning: invalid index of a 0-dim tensor. This will be an error in PyTorch 0.5. Use tensor.item() to convert a 0-dim tensor to a Python number
  vf_loss += value_loss.detach().cpu()[0]
/home/sigai/Documents/Projects/Object-Recognition/assignment5_materials/Assignment5_PPO/Assignment5/agent.py:256: UserWarning: invalid index of a 0-dim tensor. This will be an error in PyTorch 0.5. Use tensor.item() to convert a 0-dim tensor to a Python number
  ent_total += ent.detach().cpu()[0]


Iteration 1: Policy loss: 0.015861. Value loss: 1.545248. Entropy: 1.778339.
Iteration 2: Policy loss: 0.003832. Value loss: 1.441768. Entropy: 1.771869.
Iteration 3: Policy loss: 0.000260. Value loss: 1.198427. Entropy: 1.772347.
Training network. lr: 0.000250. clip: 0.100000
Iteration 4: Policy loss: 0.012576. Value loss: 4.035398. Entropy: 1.781936.
Iteration 5: Policy loss: 0.007540. Value loss: 3.012988. Entropy: 1.782049.
Iteration 6: Policy loss: 0.005987. Value loss: 2.157456. Entropy: 1.779896.
now time :  2019-02-22 23:36:31.975633
episode: 1   score: 50.0  epsilon: 1.0    steps: 375  evaluation reward: nan


/usr/local/lib/python3.5/dist-packages/numpy/core/fromnumeric.py:2920: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/usr/local/lib/python3.5/dist-packages/numpy/core/_methods.py:85: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


...

episode: 15954   score: 405.0  epsilon: 1.0    steps: 521  evaluation reward: 378.15
Training network. lr: 0.000025. clip: 0.010112
Iteration 42634: Policy loss: 0.001162. Value loss: 4.504813. Entropy: 1.163585.
Iteration 42635: Policy loss: 0.002739. Value loss: 3.535552. Entropy: 1.126000.
Iteration 42636: Policy loss: 0.002341. Value loss: 3.209723. Entropy: 1.140029.
episode: 15955   score: 390.0  epsilon: 1.0    steps: 838  evaluation reward: 377.7
Training network. lr: 0.000025. clip: 0.010112
Iteration 42637: Policy loss: 0.001748. Value loss: 7.662657. Entropy: 1.297720.
Iteration 42638: Policy loss: 0.005906. Value loss: 5.849904. Entropy: 1.286700.
Iteration 42639: Policy loss: 0.008657. Value loss: 5.361269. Entropy: 1.308409.
Training network. lr: 0.000025. clip: 0.010112
Iteration 42640: Policy loss: 0.000876. Value loss: 3.734611. Entropy: 1.308383.
Iteration 42641: Policy loss: 0.002037. Value loss: 3.034439. Entropy: 1.289336.
Iteration 42642: Policy loss: 0.001537. Va

Iteration 42699: Policy loss: 0.006875. Value loss: 4.983131. Entropy: 1.274072.
Training network. lr: 0.000025. clip: 0.010112
Iteration 42700: Policy loss: 0.000761. Value loss: 3.059042. Entropy: 1.279528.
Iteration 42701: Policy loss: 0.001551. Value loss: 2.548738. Entropy: 1.285938.
Iteration 42702: Policy loss: 0.001295. Value loss: 2.297123. Entropy: 1.288720.
episode: 15977   score: 635.0  epsilon: 1.0    steps: 301  evaluation reward: 355.8
Training network. lr: 0.000025. clip: 0.010112
Iteration 42703: Policy loss: 0.000346. Value loss: 3.105695. Entropy: 1.381998.
Iteration 42704: Policy loss: 0.001827. Value loss: 2.625186. Entropy: 1.378200.
Iteration 42705: Policy loss: 0.001899. Value loss: 2.233175. Entropy: 1.381790.
episode: 15978   score: 420.0  epsilon: 1.0    steps: 5  evaluation reward: 359.0
episode: 15979   score: 490.0  epsilon: 1.0    steps: 850  evaluation reward: 360.0
episode: 15980   score: 285.0  epsilon: 1.0    steps: 938  evaluation reward: 362.55
Trai

Training network. lr: 0.000025. clip: 0.010112
Iteration 42763: Policy loss: 0.000948. Value loss: 4.232555. Entropy: 0.971476.
Iteration 42764: Policy loss: 0.000675. Value loss: 3.390482. Entropy: 0.974644.
Iteration 42765: Policy loss: 0.002024. Value loss: 3.095367. Entropy: 0.975824.
now time :  2019-02-23 14:19:52.778515
episode: 16001   score: 615.0  epsilon: 1.0    steps: 780  evaluation reward: 350.45
Training network. lr: 0.000025. clip: 0.010112
Iteration 42766: Policy loss: 0.001729. Value loss: 8.632474. Entropy: 0.923833.
Iteration 42767: Policy loss: 0.002407. Value loss: 7.363304. Entropy: 0.917673.
Iteration 42768: Policy loss: 0.003344. Value loss: 6.685234. Entropy: 0.924593.
episode: 16002   score: 575.0  epsilon: 1.0    steps: 195  evaluation reward: 352.5
episode: 16003   score: 300.0  epsilon: 1.0    steps: 1003  evaluation reward: 354.75
Training network. lr: 0.000025. clip: 0.010112
Iteration 42769: Policy loss: -0.000249. Value loss: 3.279787. Entropy: 1.23321

Iteration 42828: Policy loss: 0.002402. Value loss: 2.189319. Entropy: 1.391891.
episode: 16023   score: 285.0  epsilon: 1.0    steps: 198  evaluation reward: 354.6
episode: 16024   score: 420.0  epsilon: 1.0    steps: 552  evaluation reward: 352.25
Training network. lr: 0.000025. clip: 0.010112
Iteration 42829: Policy loss: 0.002103. Value loss: 7.919713. Entropy: 1.091361.
Iteration 42830: Policy loss: 0.003896. Value loss: 6.273179. Entropy: 1.083237.
Iteration 42831: Policy loss: 0.005176. Value loss: 5.523204. Entropy: 1.079673.
episode: 16025   score: 465.0  epsilon: 1.0    steps: 511  evaluation reward: 353.05
Training network. lr: 0.000025. clip: 0.010112
Iteration 42832: Policy loss: 0.000859. Value loss: 4.419936. Entropy: 1.122627.
Iteration 42833: Policy loss: 0.004967. Value loss: 2.909539. Entropy: 1.125288.
Iteration 42834: Policy loss: 0.003536. Value loss: 2.549416. Entropy: 1.110096.
episode: 16026   score: 320.0  epsilon: 1.0    steps: 831  evaluation reward: 355.8
e

Training network. lr: 0.000025. clip: 0.010112
Iteration 42892: Policy loss: 0.001083. Value loss: 3.180392. Entropy: 1.208713.
Iteration 42893: Policy loss: 0.000485. Value loss: 2.807947. Entropy: 1.229712.
Iteration 42894: Policy loss: 0.001475. Value loss: 2.313392. Entropy: 1.197828.
Training network. lr: 0.000025. clip: 0.010112
Iteration 42895: Policy loss: 0.000002. Value loss: 2.919965. Entropy: 1.346479.
Iteration 42896: Policy loss: 0.002212. Value loss: 2.888144. Entropy: 1.328497.
Iteration 42897: Policy loss: 0.002699. Value loss: 2.413810. Entropy: 1.350518.
episode: 16048   score: 230.0  epsilon: 1.0    steps: 351  evaluation reward: 367.45
Training network. lr: 0.000025. clip: 0.010112
Iteration 42898: Policy loss: 0.000642. Value loss: 3.295203. Entropy: 1.320478.


In [ ]:
torch.save(agent.policy_net, "./save_model/spaceinvaders_ppo")